In [ ]:

import librosa
import numpy as np
import torch
import IPython
from music2latent4 import Inferencer
import soundfile as sf

# Initialize the Inferencer
encdec = Inferencer()

# Load an example audio file (or use your own!)
#audio_path = librosa.example('trumpet')
audio_path="/home/eloi/projects/project_mfm_eloi/src/audio_examples/9220_ld_multi.wav"
wv, sr=sf.read(audio_path, dtype='float32')
#wv, sr = librosa.load(audio_path, sr=44100)  # Ensure 44.1kHz sample rate
wv=torch.from_numpy(wv).permute(1,0)  # Add batch dimension

wv= wv.unsqueeze(0)  # Add a batch dimension



print(wv.shape)
length=2**19+1024
start=15*sr
end=start+length
wv=wv[...,start:end]  # Truncate to 5 seconds for faster processing


print("wv", wv.shape)

# Encode the audio
latent = encdec.encode(wv)

def latent2seq(latent):
    """
    Convert the latent representation to a sequence of latent vectors.
    """
    # Reshape the latent representation to match the expected input shape
    #latent = latent.view(latent.size(0), -1)
    #latent = latent.view(latent.size(0), latent.size(1), -1)
    latent = latent.view(latent.size(0),-1, latent.size(-1))
    return latent

def seq2latent(latent_sequence):
    """
    Convert the sequence of latent vectors back to the original latent representation.
    """
    # Reshape the latent sequence to match the expected output shape
    #latent = latent_sequence.view(latent_sequence.size(0), -1, 64)
    #latent = latent_sequence.view(latent_sequence.size(0),latent_sequence.size(1), -1, 64)

    latent = latent_sequence.view(latent_sequence.size(0), -1,8, latent_sequence.size(-1))
    return latent


wv_rec = encdec.decode(latent)

print("wv_rec", wv_rec.shape)

# Listen to the original and reconstructed audio 
wv=wv.squeeze(0)
print('Original')
IPython.display.display(IPython.display.Audio(wv, rate=sr, normalize=False))
print('Reconstructed')
wv_rec = wv_rec.squeeze(0)
IPython.display.display(IPython.display.Audio(wv_rec.squeeze().cpu().numpy(), rate=sr, normalize=False))


torch.Size([1, 2, 11065214])
wv torch.Size([1, 2, 525312])
latent torch.Size([1, 128, 64])
wv_rec torch.Size([1, 2, 525312])
Original


Reconstructed


In [ ]:

def generate_pink_noise(shape, device='cpu'):
    """
    Generate pink noise with 1/f frequency scaling for a batch of stereo signals.
    
    Args:
        shape (tuple): Shape of the noise signal (B, 2, T).
        device (str): Device for tensor computation ('cpu' or 'cuda').
    
    Returns:
        torch.Tensor: Pink noise signal with shape (B, 2, T).
    """
    B, C, T = shape
    
    # Generate white noise
    white_noise = torch.randn(B, C, T, device=device)
    
    # Perform FFT to move to frequency domain
    fft = torch.fft.rfft(white_noise, dim=-1)
    
    # Generate frequency bins
    freqs = torch.fft.rfftfreq(T, d=1.0)
    
    # Scale the amplitude by 1/sqrt(frequency) to approximate pink noise
    # Avoid division by zero by clamping frequencies to a minimum value
    fft /= torch.sqrt(torch.clamp(freqs, min=1e-6)).unsqueeze(0).unsqueeze(0)
    
    # Perform inverse FFT to return to time domain
    pink_noise = torch.fft.irfft(fft, n=T, dim=-1)
    
    return pink_noise

def add_pink_noise(signal, snr_db):
    """
    Add pink noise to a signal based on the desired SNR.
    
    Args:
        signal (torch.Tensor): Original signal with shape (B, 2, T).
        snr_db (float): Desired Signal-to-Noise Ratio in decibels.
    
    Returns:
        torch.Tensor: Noisy signal with the specified SNR.
    """
    # Calculate signal power
    signal_power = torch.mean(signal ** 2, dim=-1, keepdim=True)
    
    # Calculate noise power based on desired SNR
    snr_linear = 10 ** (snr_db / 10)
    noise_power = signal_power / snr_linear
    
    # Generate pink noise
    pink_noise = generate_pink_noise(signal.shape, device=signal.device)
    
    # Scale pink noise to achieve the desired noise power
    noise_scaling_factor = torch.sqrt(noise_power / torch.mean(pink_noise ** 2, dim=-1, keepdim=True))
    scaled_noise = pink_noise * noise_scaling_factor
    
    # Add scaled noise to the original signal
    noisy_signal = signal + scaled_noise
    
    return noisy_signal

wv=torch.stack([wv, wv], dim=0)  # Duplicate the waveform to create stereo signal
#wv shape *(B, 2, T)
SNR_mean= -10
SNR_std=  2  
SNR= torch.randn(wv.shape[0], device=wv.device) * SNR_std + SNR_mean

print("SNR", SNR)
wvnoisy = add_pink_noise(wv, snr_db=SNR)  # Add pink noise with SNR of 10 dB

latent = encdec.encode(wvnoisy)

wv_rec = encdec.decode(latent)

print("wv_rec", wv_rec.shape)

# Listen to the original and reconstructed audio 
wvnoisy=wvnoisy.squeeze(0)
print('Original')
IPython.display.display(IPython.display.Audio(wvnoisy, rate=sr, normalize=True))
print('Reconstructed')
wv_rec = wv_rec.squeeze(0)
IPython.display.display(IPython.display.Audio(wv_rec.squeeze().cpu().numpy(), rate=sr, normalize=True))

SNR tensor([ -6.6078, -12.5409])


ValueError: too many values to unpack (expected 3)

In [12]:
wv=wv.squeeze(0)

In [6]:
print(wv.shape)

torch.Size([2, 525312])


In [3]:
def read_wav_segment(file_path, start, end, dtype="float32"):
    """
    Reads a specific segment from a .wav file efficiently.

    Args:
        file_path (str): Path to the .wav file.
        start (int): Start frame index.
        end (int): End frame index.

    Returns:
        numpy.ndarray: Audio data for the specified segment.
        int: Sample rate of the audio file.
    """
    # Open the .wav file
    with sf.SoundFile(file_path) as audio_file:
        # Read only the required frames
        audio_file.seek(start)
        data = audio_file.read(frames=end-start, dtype=dtype)
        samplerate = audio_file.samplerate

    return data, samplerate

def get_audio_length(file_path):
    """
    Retrieves the length of an audio file in seconds and frames.

    Args:
        file_path (str): Path to the audio file.

    Returns:
        float: Length of the audio file in seconds.
        int: Total number of frames in the audio file.
        int: Sample rate of the audio file.
    """
    with sf.SoundFile(file_path) as audio_file:
        total_frames = len(audio_file)  # Total number of frames
        samplerate = audio_file.samplerate  # Sample rate
        duration = total_frames / samplerate  # Duration in seconds

    return duration, total_frames, samplerate

audio_path="/home/eloi/projects/project_mfm_eloi/src/audio_examples/9220_ld_multi.wav"

duration, total_frames, samplerate = get_audio_length(audio_path)
start = 175*samplerate
end = start + 2**19+1024
#end = 2**19+1024

x, sr = read_wav_segment(audio_path, start, end)
x=torch.from_numpy(x).permute(1,0)  # Add batch dimension
rms= torch.sqrt(torch.mean(x**2, dim=-1))
rms_dB = 20 * torch.log10(rms)  # Convert to dB
print("rms", rms_dB)
IPython.display.display(IPython.display.Audio(x, rate=sr, normalize=False))

rms tensor([-20.4003, -20.4316])


In [4]:
print("x", x.shape)


x torch.Size([2, 525312])


In [8]:
x=x.mean(dim=0)  # Average across the batch dimension
y=torch.roll(x, shifts=100, dims=-1)  # Shift the tensor along the last dimension
N = x.size(-1)
M = y.size(-1)

X = torch.fft.rfft(x, n=N + M - 1)
Y = torch.fft.rfft(y, n=N + M - 1)
corr = torch.fft.irfft(X.conj() * Y)

In [9]:
print(corr.shape)

torch.Size([1050622])


In [10]:

corr

tensor([ -802.3566,  -583.9730,  -356.5474,  ..., -1355.2931, -1190.1633,
        -1005.3810])

In [14]:
import plotly.express as px

px.line(x=torch.arange(corr[0:3000].shape[-1]), y=corr[0:3000].cpu().numpy(), title="Correlation", labels={'x': 'Sample', 'y': 'Amplitude'}).show()